# Import packages

In [1]:
%%time
import folium
import requests
import random

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from datetime import datetime
from datetime import timedelta

CPU times: user 2.13 s, sys: 272 ms, total: 2.4 s
Wall time: 16.5 s


# Data cleaning Milkrun

In [3]:
%%time
# read as DataFrame
milk_df = pd.read_excel("../Data/Milkrun Order Data.xlsx", engine='openpyxl')
print(milk_df.shape)
milk_df.head()

(77585, 21)
CPU times: user 22.2 s, sys: 163 ms, total: 22.4 s
Wall time: 26.1 s


merchant_id merchant_name  driver_id   driver_name  vehicle_type  order_id  \
0            2     RTH Store        1.0  Harry Callum           0.0  10300319   
1            2     RTH Store        NaN           NaN           NaN  10300324   
2            2     RTH Store        NaN           NaN           NaN  10300328   
3            2     RTH Store        1.0  Harry Callum           0.0  10300328   
4            2     RTH Store        1.0  Harry Callum           0.0  10300450   

                              pick_up_address  \
0  11 Keng Cheow St, #03-06, Singapore 059608   
1  11 Keng Cheow St, #03-06, Singapore 059608   
2  11 Keng Cheow St, #03-06, Singapore 059608   
3  11 Keng Cheow St, #03-06, Singapore 059608   
4  11 Keng Cheow St, #03-06, Singapore 059608   

                          delivery_address  paid_fee delivery_distance  ...  \
0              12 Keng Cheow St, Singapore    1.5000              51 m  ...   
1       55 Lengkok Bahru, Singapore 151055    2.1045            4.2 km  ...   
2        54 Chin Swee Rd, Singapore 160054    1.5000            0.7 km  ...   
3  444 Pasir Ris Drive 6, Singapore 510444   10.0715           20.1 km  ...   
4           23 Jln Besar, Singapore 208794    1.5790            3.2 km  ...   

             submitted_at             accepted_at driver_arrived_at  \
0 2020-10-30 03:19:37.306 2020-10-30 03:20:32.488               NaT   
1 2020-10-30 03:24:48.049                     NaT               NaT   
2 2020-10-30 03:28:33.642                     NaT               NaT   
3 2020-10-30 03:28:58.560 2020-10-30 03:29:23.535               NaT   
4 2020-10-30 04:51:33.437 2020-10-30 04:53:01.459               NaT   

                picked_at            delivered_at            cancelled_at  \
0 2020-10-30 03:20:54.820 2020-10-30 03:22:08.879                     NaT   
1                     NaT                     NaT 2020-10-30 03:25:43.134   
2                     NaT                     NaT 2020-10-30 03:29:16.270   
3 2020-10-30 03:29:37.350 2020-10-30 04:49:21.164                     NaT   
4 2020-10-30 05:59:20.203 2020-10-30 06:26:59.927                     NaT   

  driver_paid_fee  car_only  tips  Restaurant Area  
0         0.25000     False   0.0              NaN  
1             NaN     False   0.0              NaN  
2             NaN     False   0.0              NaN  
3         4.53575     False   0.0              NaN  
4         0.28950     False   0.0              NaN  

[5 rows x 21 columns]

In [4]:
# restaurant with customer locations greater than 300
pickup_address_df = milk_df['pick_up_address'].value_counts().to_frame('Number')
pickup_address_list = list(pickup_address_df[pickup_address_df['Number'] > 300].index)
pickup_address_list

['Breadtalk Ihq, 30 Tai Seng St, Singapore 534013, Singapore',
 'Ghim Moh Market & Food Centre',
 '37 Cuppage Rd, Singapore 229460, Singapore',
 '219 Bedok Central, Block 219, Êñ∞Âä†Âù° 460219',
 'Maxwell Food Centre',
 '22 New Industrial Road, Singapore',
 '36 Boat Quay, Singapore 049825, Singapore',
 'AMK628',
 'Bukit Timah Market & Food Centre',
 'Hong Lim Food Centre',
 'Bedok Interchange Hawker Centre',
 'Old Airport Road Food Centre',
 'Kovan Food Centre (209 Hougang Street 21)',
 '54 South Bridge Rd, Singapore 058685, Singapore',
 '21 Amber Rd, Singapore 439870',
 'Alexandra Village Food Centre',
 '263 Upp Thomson Rd, Singapore 574390, Singapore',
 'Tarte by Cheryl Koh (Shaw)\n1 Scotts Road, Shaw Centre, #02-05\nSingapore, 228208\nTel: 62353225\nGST Reg. No.: M201144779',
 'Bukit Merah View Market & Hawker Centre',
 'Lorong 8 Toa Payoh Hawker Centre',
 'Tiong Bahru Market',
 '632 Bedok Reservoir Rd, Singapore 470632, Singapore',
 'Chinatown Complex Food Centre',
 '86 Circular Rd

## Get coordinate of address

In [5]:
def get_coordinate(address):
    '''
    Input: 
    - address (string)
    Output: 
    - latitude and longitude
    '''
    req = requests.get('https://developers.onemap.sg/commonapi/search?searchVal=' + address + '&returnGeom=Y&getAddrDetails=Y&pageNum=1')
    resultsdict = eval(req.text)
    if len(resultsdict['results']) > 0:
        return float(resultsdict['results'][0]['LATITUDE']), float(resultsdict['results'][0]['LONGITUDE'])
    else:
        pass

In [6]:
def get_postcode(address):
    '''
    Input:
    - address
    Output:
    - postcode (string)
    '''
    ans = ""
    str_list = address.replace(",","").split(" ")
    for s in reversed(str_list):
        if s.isnumeric() and len(s) == 6:
            ans = s
            break
    
    return ans

In [7]:
%%time
# read postcode dataframe
postcode_df = pd.read_json('../Data/singpostcode.json')
postcode_df.head()

CPU times: user 981 ms, sys: 151 ms, total: 1.13 s
Wall time: 8.29 s


ADDRESS BLK_NO  \
0  1 STRAITS BOULEVARD SINGAPORE CHINESE CULTURAL...      1   
1  11A STRAITS BOULEVARD TEMPORARY SITE OFFICE SI...    11A   
2           5A MARINA GARDENS DRIVE SINGAPORE 018910     5A   
3  2 CENTRAL BOULEVARD CENTRAL BOULEVARD TOWERS S...      2   
4  21 PARK STREET MARINA BAY MRT STATION SINGAPOR...     21   

                            BUILDING  LATITUDE   LONGITUDE  LONGTITUDE  \
0  SINGAPORE CHINESE CULTURAL CENTRE  1.275805  103.849615  103.849615   
1              TEMPORARY SITE OFFICE  1.274950  103.851665  103.851665   
2                                NIL  1.279587  103.868956  103.868956   
3           CENTRAL BOULEVARD TOWERS  1.279744  103.851591  103.851591   
4      MARINA BAY MRT STATION (NS27)  1.276409  103.854595  103.854595   

   POSTAL             ROAD_NAME                                 SEARCHVAL  \
0  018906     STRAITS BOULEVARD         SINGAPORE CHINESE CULTURAL CENTRE   
1  018907     STRAITS BOULEVARD                     TEMPORARY SITE OFFICE   
2  018910  MARINA GARDENS DRIVE  5A MARINA GARDENS DRIVE SINGAPORE 018910   
3  018916     CENTRAL BOULEVARD                  CENTRAL BOULEVARD TOWERS   
4  018925           PARK STREET             MARINA BAY MRT STATION (NS27)   

             X            Y  
0  29813.66349  28697.52076  
1  30041.83890  28602.98724  
2  31966.12079  29115.75337  
3  30033.60446  29133.10468  
4  30367.92624  28764.38143

In [8]:
# get {postcode: coordinate} dict
postcode_coordinate_dict = pd.Series(list(zip(postcode_df.LATITUDE.values, postcode_df.LONGITUDE.values)), index=postcode_df.POSTAL).to_dict()
for k, v in postcode_coordinate_dict.items():
    postcode_coordinate_dict[k] = (v[0].round(9), v[1].round(9))
    
postcode_coordinate_dict

{'018906': (1.275804635, 103.849615),
 '018907': (1.274949694, 103.8516652),
 '018910': (1.279586788, 103.8689557),
 '018916': (1.27974389, 103.8515913),
 '018925': (1.276427355, 103.8545978),
 '018926': (1.276251464, 103.8554472),
 '018927': (1.275241279, 103.853659),
 '018928': (1.277681396, 103.8501573),
 '018929': (1.275194574, 103.8551738),
 '018930': (1.275358332, 103.8670278),
 '018935': (1.277526289, 103.8529353),
 '018936': (1.278032422, 103.8528832),
 '018937': (1.277336813, 103.8523824),
 '018940': (1.280165471, 103.8562877),
 '018946': (1.270044929, 103.8573239),
 '018947': (1.266182751, 103.860463),
 '018948': (1.271027036, 103.8624475),
 '018951': (1.280884109, 103.8698853),
 '018953': (1.284620463, 103.8647354),
 '018955': (1.28432373, 103.8595636),
 '018956': (1.282407043, 103.8583927),
 '018957': (1.28179751, 103.859037),
 '018958': (1.284234913, 103.8589822),
 '018959': (1.279392556, 103.8586727),
 '018960': (1.27884624, 103.8511636),
 '018961': (1.278307296, 103.8507

In [9]:
def get_address_coordinate_dict(address_list, postcode_coordinate_dict):
    '''
    Inputs:
    - pickup_address_list: list of address string
    - postcode_coordinate_dict: {key: postcode, value: (latitude, longitude)}
    Output:
    - dict: {key: address, value: (latitude, longitude)}
    '''
    coordinates_dict = {}
    postcode_list = postcode_coordinate_dict.keys()
    count = 0
    
    for address in address_list:
        # find through postcode
        ad_post = get_postcode(address)
        if (ad_post != "") and (ad_post in postcode_list):
            count = count + 1
            coordinates_dict[address] = postcode_coordinate_dict[ad_post]
            continue
        
        # find through get_coordinate (web service)
        try:
            if len(get_coordinate(address)) > 0:
                count = count + 1
                coordinates_dict[address] = get_coordinate(address)
        except:
            continue

    print('Total Number of Addresses With No Coordinates:', len(address_list) - count)
    
    return coordinates_dict

In [10]:
%%time
# find coordinate for pickup address
pickup_address_coordinates_dict = get_address_coordinate_dict(pickup_address_list, postcode_coordinate_dict)
print("Total number of address coordinate find: ", len(pickup_address_coordinates_dict))

Total Number of Addresses With No Coordinates: 13
Total number of address coordinate find:  44
CPU times: user 819 ms, sys: 65.5 ms, total: 885 ms
Wall time: 7.33 s


## Delivery distance calculation

In [11]:
# select dataframe with selected pickup address list
select_df = milk_df[milk_df['pick_up_address'].isin(pickup_address_coordinates_dict.keys())]
print(select_df.shape)
select_df.head()

(32842, 21)


merchant_id    merchant_name  driver_id   driver_name  vehicle_type  \
135           41  CSC Manzhu Cafe        NaN           NaN           NaN   
136           39             CSC       186.0  Zoey MilkRun           1.0   
200           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
201           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
205           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   

    order_id                pick_up_address  \
135   CS0001  21 Amber Rd, Singapore 439870   
136   CS0001  21 Amber Rd, Singapore 439870   
200   CS0010  21 Amber Rd, Singapore 439870   
201   CS0011  21 Amber Rd, Singapore 439870   
205   CS0014  21 Amber Rd, Singapore 439870   

                         delivery_address  paid_fee delivery_distance  ...  \
135          1 Robin Rd, Singapore 258176    18.161           10.3 km  ...   
136           3 Haig Rd, Singapore 430003     5.000            1.5 km  ...   
200                      Singapore 440047     3.500            1.5 km  ...   
201                      Singapore 440047     3.500            1.5 km  ...   
205  3 Haig Rd, Block 3, Singapore 430003     3.500            1.5 km  ...   

               submitted_at             accepted_at driver_arrived_at  \
135 2021-01-12 15:44:25.847                     NaT               NaT   
136 2021-01-12 15:44:29.308 2021-01-12 15:44:59.341               NaT   
200 2021-01-27 12:39:18.832 2021-01-27 13:03:25.926               NaT   
201 2021-01-27 13:14:34.798 2021-01-27 13:14:43.726               NaT   
205 2021-01-27 18:30:06.653 2021-01-27 18:38:46.524               NaT   

                  picked_at            delivered_at            cancelled_at  \
135                     NaT                     NaT                     NaT   
136 2021-01-12 15:45:20.555 2021-01-12 15:46:15.883                     NaT   
200                     NaT                     NaT 2021-01-27 13:03:44.777   
201 2021-01-27 13:32:34.059 2021-01-27 13:46:32.818                     NaT   
205 2021-01-27 18:47:17.782 2021-01-27 18:59:33.035                     NaT   

    driver_paid_fee  car_only  tips  Restaurant Area  
135             NaN     False   0.0              NaN  
136            4.25     False   0.0              NaN  
200            2.75     False   0.0              NaN  
201            2.75     False   0.0              NaN  
205            2.75     False   0.0              NaN  

[5 rows x 21 columns]

### Find pickup coordinate and delivery coordinate

In [12]:
%%time

select_df['pick_up_coordinate'] = ""
select_df['delivery_coordinate'] = ""

# iterate the rows of milkrun dataframe, and construct two new columns: "pickup coordinate", and "delivery coordinate"
for index, row in select_df.iterrows():
    p_address = row['pick_up_address']
    d_address = row['delivery_address']
    
    # get pickup coordinate
    select_df.at[index, 'pick_up_coordinate'] = pickup_address_coordinates_dict[p_address]
    
    '''
    get delivery coordinate
    '''
    # get coordinate from postcode
    d_post = get_postcode(str(d_address)) 
    if (d_post != "") and (d_post in postcode_coordinate_dict.keys()):
        select_df.at[index, 'delivery_coordinate'] = postcode_coordinate_dict[d_post]
        continue
    
    # get coordinate from web service
    try:
        if len(get_coordinate(d_address)) > 0:
            select_df.at[index, 'delivery_coordinate'] = (get_coordinate(d_address))
    except:
        continue

# check
select_df.head()

/Users/larcuser/opt/anaconda3/envs/yjfkd/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/Users/larcuser/opt/anaconda3/envs/yjfkd/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


CPU times: user 34.5 s, sys: 2.66 s, total: 37.2 s
Wall time: 3min 12s


merchant_id    merchant_name  driver_id   driver_name  vehicle_type  \
135           41  CSC Manzhu Cafe        NaN           NaN           NaN   
136           39             CSC       186.0  Zoey MilkRun           1.0   
200           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
201           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
205           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   

    order_id                pick_up_address  \
135   CS0001  21 Amber Rd, Singapore 439870   
136   CS0001  21 Amber Rd, Singapore 439870   
200   CS0010  21 Amber Rd, Singapore 439870   
201   CS0011  21 Amber Rd, Singapore 439870   
205   CS0014  21 Amber Rd, Singapore 439870   

                         delivery_address  paid_fee delivery_distance  ...  \
135          1 Robin Rd, Singapore 258176    18.161           10.3 km  ...   
136           3 Haig Rd, Singapore 430003     5.000            1.5 km  ...   
200                      Singapore 440047     3.500            1.5 km  ...   
201                      Singapore 440047     3.500            1.5 km  ...   
205  3 Haig Rd, Block 3, Singapore 430003     3.500            1.5 km  ...   

    driver_arrived_at               picked_at            delivered_at  \
135               NaT                     NaT                     NaT   
136               NaT 2021-01-12 15:45:20.555 2021-01-12 15:46:15.883   
200               NaT                     NaT                     NaT   
201               NaT 2021-01-27 13:32:34.059 2021-01-27 13:46:32.818   
205               NaT 2021-01-27 18:47:17.782 2021-01-27 18:59:33.035   

               cancelled_at driver_paid_fee car_only tips  Restaurant Area  \
135                     NaT             NaN    False  0.0              NaN   
136                     NaT            4.25    False  0.0              NaN   
200 2021-01-27 13:03:44.777            2.75    False  0.0              NaN   
201                     NaT            2.75    False  0.0              NaN   
205                     NaT            2.75    False  0.0              NaN   

             pick_up_coordinate         delivery_coordinate  
135  (1.299306492, 103.9005769)  (1.318917756, 103.8287018)  
136  (1.299306492, 103.9005769)   (1.31170259, 103.8973795)  
200  (1.299306492, 103.9005769)  (1.305723545, 103.9125305)  
201  (1.299306492, 103.9005769)  (1.305723545, 103.9125305)  
205  (1.299306492, 103.9005769)   (1.31170259, 103.8973795)  

[5 rows x 23 columns]

In [13]:
# check delivery coordinate extraction result
(select_df['delivery_coordinate'] != "").sum(), (select_df['delivery_coordinate'] == "").sum()

(30964, 1878)

### Calculate distance based on coordinates

In [15]:
# calculate distance
import haversine as hs

select_df['coordinate_distance'] = 0.0

for index, row in select_df.iterrows():
    try:
        select_df.at[index, 'coordinate_distance'] = hs.haversine(row['pick_up_coordinate'], row['delivery_coordinate'])
    except:
        continue

select_df.head()

/Users/larcuser/opt/anaconda3/envs/yjfkd/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


merchant_id    merchant_name  driver_id   driver_name  vehicle_type  \
135           41  CSC Manzhu Cafe        NaN           NaN           NaN   
136           39             CSC       186.0  Zoey MilkRun           1.0   
200           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
201           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   
205           41  CSC Manzhu Cafe       12.0     mars rawi           0.0   

    order_id                pick_up_address  \
135   CS0001  21 Amber Rd, Singapore 439870   
136   CS0001  21 Amber Rd, Singapore 439870   
200   CS0010  21 Amber Rd, Singapore 439870   
201   CS0011  21 Amber Rd, Singapore 439870   
205   CS0014  21 Amber Rd, Singapore 439870   

                         delivery_address  paid_fee delivery_distance  ...  \
135          1 Robin Rd, Singapore 258176    18.161           10.3 km  ...   
136           3 Haig Rd, Singapore 430003     5.000            1.5 km  ...   
200                      Singapore 440047     3.500            1.5 km  ...   
201                      Singapore 440047     3.500            1.5 km  ...   
205  3 Haig Rd, Block 3, Singapore 430003     3.500            1.5 km  ...   

                  picked_at            delivered_at            cancelled_at  \
135                     NaT                     NaT                     NaT   
136 2021-01-12 15:45:20.555 2021-01-12 15:46:15.883                     NaT   
200                     NaT                     NaT 2021-01-27 13:03:44.777   
201 2021-01-27 13:32:34.059 2021-01-27 13:46:32.818                     NaT   
205 2021-01-27 18:47:17.782 2021-01-27 18:59:33.035                     NaT   

    driver_paid_fee car_only tips Restaurant Area          pick_up_coordinate  \
135             NaN    False  0.0             NaN  (1.299306492, 103.9005769)   
136            4.25    False  0.0             NaN  (1.299306492, 103.9005769)   
200            2.75    False  0.0             NaN  (1.299306492, 103.9005769)   
201            2.75    False  0.0             NaN  (1.299306492, 103.9005769)   
205            2.75    False  0.0             NaN  (1.299306492, 103.9005769)   

            delivery_coordinate  coordinate_distance  
135  (1.318917756, 103.8287018)             8.282306  
136   (1.31170259, 103.8973795)             1.423476  
200  (1.305723545, 103.9125305)             1.508296  
201  (1.305723545, 103.9125305)             1.508296  
205   (1.31170259, 103.8973795)             1.423476  

[5 rows x 24 columns]

In [16]:
# records with distance in 5km and not equals to 0
select_df = select_df[(select_df['coordinate_distance'] <= 5.0) & (select_df['coordinate_distance'] != 0.0)]
select_df.shape

(19473, 24)

In [17]:
select_df['pick_up_address'].value_counts()

Ghim Moh Market & Food Centre                                                  2044
Maxwell Food Centre                                                            1288
Hong Lim Food Centre                                                            932
Old Airport Road Food Centre                                                    919
219 Bedok Central, Block 219, Êñ∞Âä†Âù° 460219                                  798
Kovan Food Centre (209 Hougang Street 21)                                       754
Bedok Interchange Hawker Centre                                                 753
Bukit Timah Market & Food Centre                                                752
37 Cuppage Rd, Singapore 229460, Singapore                                      752
21 Amber Rd, Singapore 439870                                                   722
Alexandra Village Food Centre                                                   710
Tiong Bahru Market                                                          

## Update pickup address

In [18]:
# remove restaurants far away from the study area
too_far_restaurant = ['Changi Village Hawker Centre', 'Yishun Park Hawker Centre', 'Chong Pang Food Centre', 
                      '18 Tampines Ind Cres, Singapore 528605, Singapore']

restaurant_list = [r for r in list(select_df['pick_up_address'].value_counts()[:30].index) if r not in too_far_restaurant]
restaurant_list

['Ghim Moh Market & Food Centre',
 'Maxwell Food Centre',
 'Hong Lim Food Centre',
 'Old Airport Road Food Centre',
 '219 Bedok Central, Block 219, Êñ∞Âä†Âù° 460219',
 'Kovan Food Centre (209 Hougang Street 21)',
 'Bedok Interchange Hawker Centre',
 'Bukit Timah Market & Food Centre',
 '37 Cuppage Rd, Singapore 229460, Singapore',
 '21 Amber Rd, Singapore 439870',
 'Alexandra Village Food Centre',
 'Tiong Bahru Market',
 '632 Bedok Reservoir Rd, Singapore 470632, Singapore',
 'Lorong 8 Toa Payoh Hawker Centre',
 'Bukit Merah View Market & Hawker Centre',
 'Amoy Street Food Centre',
 'Golden Mile Food Centre',
 'Chomp Chomp',
 '66 Kg Bugis, Singapore 338987, Singapore',
 'Breadtalk Ihq, 30 Tai Seng St, Singapore 534013, Singapore',
 'Zion Riverside Food Centre',
 '36 Boat Quay, Singapore 049825, Singapore',
 '28 Maju Ave, Singapore 556698',
 '417 River Valley Rd, Singapore 248316, Singapore',
 'Our Tampines Hub Hawker Centre',
 '371 Beach Rd, Singapore 199597, Singapore',
 '54 South Bri

## Construct restaurant-customer dict, restaurant-coordinate dict

In [19]:
# construct {restaurant: (customer name, customer coordinate)} dict
restaurant_customer_dict = {r:[] for r in restaurant_list}

for r in restaurant_list:
    res_df = select_df[select_df['pick_up_address'] == r]
    restaurant_customer_dict[r] = list(zip(res_df['delivery_address'], res_df['delivery_coordinate']))

restaurant_customer_dict

{'Ghim Moh Market & Food Centre': [('589485 Singapore',
   (1.338423289, 103.7803189)),
  ('276692 Singapore', (1.317735832, 103.7785544)),
  ('276697 Singapore', (1.316284589, 103.7780899)),
  ('128044 Singapore', (1.298235909, 103.7662346)),
  ('589632 Singapore', (1.334908896, 103.7834521)),
  ('596780 Singapore', (1.338200989, 103.7644356)),
  ('140055 Singapore', (1.293382949, 103.8093307)),
  ('141087 Singapore', (1.295730427, 103.8097599)),
  ('159013 Singapore', (1.29199745, 103.8178807)),
  ('159029 Singapore', (1.292375067, 103.8228367)),
  ('131028 Singapore', (1.304915957, 103.7821881)),
  ('138614 Singapore', (1.308220427, 103.7733152)),
  ('587857 Singapore', (1.34581899, 103.7760264)),
  ('120730 Singapore', (1.304777153, 103.763122)),
  ('120710 Singapore', (1.306289119, 103.7615181)),
  ('140037 Singapore', (1.297772317, 103.7980171)),
  ('138643 Singapore', (1.301733345, 103.7900009)),
  ('271002 Singapore', (1.309344983, 103.7955594)),
  ('260006 Singapore', (1.31731

In [20]:
restaurant_coordinate_dict = {}

for r in restaurant_list:
    p_loc = select_df[select_df['pick_up_address'] == r]['pick_up_coordinate'].unique()[0]
    restaurant_coordinate_dict[r] = p_loc

restaurant_coordinate_dict

{'Ghim Moh Market & Food Centre': (1.31099663218896, 103.78823030662),
 'Maxwell Food Centre': (1.28033142727315, 103.844747227479),
 'Hong Lim Food Centre': (1.28532379322674, 103.845776735598),
 'Old Airport Road Food Centre': (1.3082518471287, 103.88580870609),
 '219 Bedok Central, Block 219, Êñ∞Âä†Âù° 460219': (1.324964578, 103.9329481),
 'Kovan Food Centre (209 Hougang Street 21)': (1.35908384091048,
  103.886055368064),
 'Bedok Interchange Hawker Centre': (1.32481816551889, 103.930544296289),
 'Bukit Timah Market & Food Centre': (1.33945242854685, 103.776007306701),
 '37 Cuppage Rd, Singapore 229460, Singapore': (1.302225777, 103.8403116),
 '21 Amber Rd, Singapore 439870': (1.299306492, 103.9005769),
 'Alexandra Village Food Centre': (1.28630594274136, 103.804492637648),
 'Tiong Bahru Market': (1.28478559810371, 103.832181546885),
 '632 Bedok Reservoir Rd, Singapore 470632, Singapore': (1.332050526,
  103.9141462),
 'Lorong 8 Toa Payoh Hawker Centre': (1.3402610461881, 103.854395

In [21]:
# check the number of delivery locations for each restaurant
for r in restaurant_list:
    print("Number of customer locations: ", len(restaurant_customer_dict[r]))

Number of customer locations:  2044
Number of customer locations:  1288
Number of customer locations:  932
Number of customer locations:  919
Number of customer locations:  798
Number of customer locations:  754
Number of customer locations:  753
Number of customer locations:  752
Number of customer locations:  752
Number of customer locations:  722
Number of customer locations:  710
Number of customer locations:  703
Number of customer locations:  701
Number of customer locations:  692
Number of customer locations:  646
Number of customer locations:  556
Number of customer locations:  515
Number of customer locations:  385
Number of customer locations:  366
Number of customer locations:  349
Number of customer locations:  325
Number of customer locations:  318
Number of customer locations:  299
Number of customer locations:  292
Number of customer locations:  263
Number of customer locations:  189
Number of customer locations:  181


## Write data to csv

In [20]:
select_df.to_csv("../Data/select_milkrun_order_data.csv")

In [22]:
import csv
with open("../Data/restaurant_list.csv", 'w') as f:
    write = csv.writer(f)
    write.writerow(restaurant_list)

In [23]:
import json

with open("../Data/restaurant_customer_dict.json", 'w') as outfile:
    json.dump(restaurant_customer_dict, outfile)

In [25]:
with open("../Data/restaurant_coordinate_dict.json", 'w') as outfile:
    json.dump(restaurant_coordinate_dict, outfile)

# Instance generation

In [22]:
order_per_time_period = pd.read_csv("../Data/order_per_time_period_2.csv")
order_per_time_period.columns = ['time_period_id', 'create_time_period', 'number']
order_per_time_period

time_period_id   create_time_period  number
0                0  2021-10-10 06:00:00       5
1                1  2021-10-10 06:45:00      15
2                2  2021-10-10 07:30:00      22
3                3  2021-10-10 08:15:00      34
4                4  2021-10-10 09:00:00      47
5                5  2021-10-10 09:45:00      63
6                6  2021-10-10 10:30:00      70
7                7  2021-10-10 11:15:00      60
8                8  2021-10-10 12:00:00      35
9                9  2021-10-10 12:45:00      28
10              10  2021-10-10 13:30:00      22
11              11  2021-10-10 14:15:00      24
12              12  2021-10-10 15:00:00      26
13              13  2021-10-10 15:45:00      40
14              14  2021-10-10 16:30:00      56
15              15  2021-10-10 17:15:00      65
16              16  2021-10-10 18:00:00      56
17              17  2021-10-10 18:45:00      46
18              18  2021-10-10 19:30:00      47
19              19  2021-10-10 20:15:00      39
20              20  2021-10-10 21:00:00      32
21              21  2021-10-10 21:45:00       8

In [23]:
# convert to dict
order_per_time_period_dict = pd.Series(order_per_time_period.number.values, index=order_per_time_period.time_period_id).to_dict()
order_per_time_period_dict

{0: 5,
 1: 15,
 2: 22,
 3: 34,
 4: 47,
 5: 63,
 6: 70,
 7: 60,
 8: 35,
 9: 28,
 10: 22,
 11: 24,
 12: 26,
 13: 40,
 14: 56,
 15: 65,
 16: 56,
 17: 46,
 18: 47,
 19: 39,
 20: 32,
 21: 8}

In [24]:
time_id_period_dict = pd.Series(order_per_time_period.create_time_period.values, index=order_per_time_period.time_period_id).to_dict()
time_id_period_dict

{0: '2021-10-10 06:00:00',
 1: '2021-10-10 06:45:00',
 2: '2021-10-10 07:30:00',
 3: '2021-10-10 08:15:00',
 4: '2021-10-10 09:00:00',
 5: '2021-10-10 09:45:00',
 6: '2021-10-10 10:30:00',
 7: '2021-10-10 11:15:00',
 8: '2021-10-10 12:00:00',
 9: '2021-10-10 12:45:00',
 10: '2021-10-10 13:30:00',
 11: '2021-10-10 14:15:00',
 12: '2021-10-10 15:00:00',
 13: '2021-10-10 15:45:00',
 14: '2021-10-10 16:30:00',
 15: '2021-10-10 17:15:00',
 16: '2021-10-10 18:00:00',
 17: '2021-10-10 18:45:00',
 18: '2021-10-10 19:30:00',
 19: '2021-10-10 20:15:00',
 20: '2021-10-10 21:00:00',
 21: '2021-10-10 21:45:00'}

In [25]:
time_period_id = list(order_per_time_period_dict.keys())
time_period_id

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21]

## Generate random seed for each restaurant

In [42]:
def restaurant_seed_generation(all_restaurants):
    '''
    Input:
    - all_restaurant: predefined instance: restaurant_list
    Output:
    - dict, {restaurant: random seed (integer value)}
    '''
    random.seed(1)
    seed_num_list = random.sample(range(1, 100), len(all_restaurants))
    restaurant_seed_dict = {all_restaurants[i]: seed_num_list[i] for i in range(len(all_restaurants))}
    
    return restaurant_seed_dict

In [43]:
restaurant_seed_num_dict = restaurant_seed_generation(restaurant_list)
restaurant_seed_num_dict

{'Ghim Moh Market & Food Centre': 18,
 'Maxwell Food Centre': 73,
 'Hong Lim Food Centre': 9,
 'Old Airport Road Food Centre': 33,
 '219 Bedok Central, Block 219, Êñ∞Âä†Âù° 460219': 16,
 'Kovan Food Centre (209 Hougang Street 21)': 64,
 'Bedok Interchange Hawker Centre': 58,
 'Bukit Timah Market & Food Centre': 61,
 '37 Cuppage Rd, Singapore 229460, Singapore': 84,
 '21 Amber Rd, Singapore 439870': 49,
 'Alexandra Village Food Centre': 27,
 'Tiong Bahru Market': 13,
 '632 Bedok Reservoir Rd, Singapore 470632, Singapore': 63,
 'Lorong 8 Toa Payoh Hawker Centre': 4,
 'Bukit Merah View Market & Hawker Centre': 50,
 'Amoy Street Food Centre': 56,
 'Golden Mile Food Centre': 78,
 'Chomp Chomp': 1,
 '66 Kg Bugis, Singapore 338987, Singapore': 93,
 'Breadtalk Ihq, 30 Tai Seng St, Singapore 534013, Singapore': 35,
 'Zion Riverside Food Centre': 30,
 '36 Boat Quay, Singapore 049825, Singapore': 76,
 '28 Maju Ave, Singapore 556698': 14,
 '417 River Valley Rd, Singapore 248316, Singapore': 41,
 '

## Order number generation

In [44]:
def order_num_generation(restaurants):
    '''
    Generate number of orders for each restaurant at each time period
    Input:
    - restaurants: list of restaurant
    Output:
    - dict {restaurant: [time period, number of orders]}
    '''
    restaurant_order_num = {r: [] for r in restaurants}
    
    for r in restaurants:
        # get restaurant seed number 
        seed_num = restaurant_seed_num_dict[r]
        random.seed(seed_num)
        alpha = random.uniform(0.5, 1.5)
        for t in time_period_id:
            order_num = int(order_per_time_period_dict[t] * alpha) + random.randint(0, 5)
            restaurant_order_num[r].append([t, order_num])
    
    return restaurant_order_num

In [45]:
# test
restaurant_order_num = order_num_generation(restaurant_list)
restaurant_order_num

{'Ghim Moh Market & Food Centre': [[0, 8],
  [1, 13],
  [2, 16],
  [3, 24],
  [4, 33],
  [5, 45],
  [6, 52],
  [7, 43],
  [8, 24],
  [9, 22],
  [10, 16],
  [11, 19],
  [12, 19],
  [13, 28],
  [14, 40],
  [15, 49],
  [16, 38],
  [17, 33],
  [18, 36],
  [19, 31],
  [20, 22],
  [21, 6]],
 'Maxwell Food Centre': [[0, 7],
  [1, 14],
  [2, 21],
  [3, 27],
  [4, 39],
  [5, 51],
  [6, 58],
  [7, 46],
  [8, 30],
  [9, 24],
  [10, 21],
  [11, 22],
  [12, 21],
  [13, 34],
  [14, 43],
  [15, 50],
  [16, 45],
  [17, 38],
  [18, 36],
  [19, 33],
  [20, 26],
  [21, 10]],
 'Hong Lim Food Centre': [[0, 6],
  [1, 16],
  [2, 22],
  [3, 33],
  [4, 50],
  [5, 60],
  [6, 69],
  [7, 61],
  [8, 36],
  [9, 30],
  [10, 21],
  [11, 25],
  [12, 29],
  [13, 42],
  [14, 58],
  [15, 62],
  [16, 58],
  [17, 47],
  [18, 46],
  [19, 42],
  [20, 33],
  [21, 12]],
 'Old Airport Road Food Centre': [[0, 10],
  [1, 17],
  [2, 25],
  [3, 39],
  [4, 55],
  [5, 71],
  [6, 78],
  [7, 65],
  [8, 42],
  [9, 33],
  [10, 27],
  [11

## Order time generation

In [46]:
def order_time_generation(t1, t2, num_orders):
    '''
    Generate random order create time in time interval [t1, t2]
    Inputs:
    - t1: start time
    - t2: end time
    - num_orders: number of orders create in [t1, t2]
    Output:
    - list of order create time
    '''
    num = 0
    output = []
    
    while num < num_orders:
        integer = random.randint(0, (t2 - t1).total_seconds())
        step = timedelta(seconds=integer)
        order_time = t1 + step
        output.append(order_time)
        num = num + 1
    
    output.sort()
    
    return [i.strftime('%Y-%m-%d %H:%M:%S') for i in output]

## Order id generation

In [47]:
def order_id_generation(time_list):
    '''
    Input:
    - time_list: list of order create time, output of Function order_time_generation
    Output:
    - list of order id
    '''
    output = []
    replace_char = "-: "
    
    for o in time_list:
        for c in replace_char:
            o = o.replace(c,"")
        output.append(o)
    
    return output

## Order location generation

In [48]:
def order_location_generation(order_id_list, restaurant):
    '''
    Input:
    - order_id_list
    - restaurant
    Output:
    - list of orders location
    '''
    o_location_list = random.sample(restaurant_customer_dict[restaurant], len(order_id_list))
    return o_location_list

## Generate instances
* 1. Given the time period, generate order time;
* 2. Given order time, generate order id;
* 3. Given order id, restaurants, and order number, generate order locations
* 4. Combine together as a dataframe.

For each restaurant：
* order_num_generation: generate orders for each time period;
* order_time_generation: for each time period, generate order create time for each order;
* order_id_generation: for each order, generate order id 
* order_location_generation: for each order, generate location information

In [49]:
restaurants_select =  ['Ghim Moh Market & Food Centre',
                       'Bukit Timah Market & Food Centre',
                       'Alexandra Village Food Centre']

In [50]:
def instance_generation(restaurants):
    '''
    Inputs:
    - restaurants： select restaurants
    Output:
    - Instance
    '''
    instance_df = pd.DataFrame(columns=['order_id', 'demand', 'creation_time', 'committed_completion_time', 
                                        'load_time', 'unload_time', 'pickup_id', 'delivery_id'])
    
    # one instance (from 6 AM to 22:30 PM)
    for time_id in time_period_id:

        # for each time period
        start = datetime.strptime(time_id_period_dict[time_id], "%Y-%m-%d %H:%M:%S")
        end = datetime.strptime(time_id_period_dict[time_id], "%Y-%m-%d %H:%M:%S") + timedelta(minutes=45)

        # for each restaurant
        for r in restaurants:
            small_df = pd.DataFrame()

            order_time_list = order_time_generation(start, end, num_orders=restaurant_order_num[r][time_id][1])
            order_id_list = order_id_generation(order_time_list)
            order_location_list = order_location_generation(order_id_list, r)
            
            small_df['order_id'] = order_id_list
            small_df['creation_time'] = order_time_list
            small_df['restaurant_name'] = [r] * len(order_id_list)
            small_df['customer_name'] = [o[0] for o in order_location_list]
            small_df['pick_up_coordinate'] = [restaurant_coordinate_dict[r]] * len(order_id_list)
            small_df['delivery_coordinate'] = [o[1] for o in order_location_list]         

            instance_df = instance_df.append(small_df, ignore_index=True)
    
    # update instance dataframe
    instance_df['demand'] = 1
    instance_df['load_time'] = 60
    instance_df['unload_time'] = 60
    instance_df['creation_time'] = pd.to_datetime(instance_df['creation_time'])
    instance_df = instance_df.sort_values(by='creation_time').reset_index()
    instance_df['committed_completion_time'] = instance_df['creation_time'] + timedelta(minutes=45)
    
    # only keep time no date
    instance_df['creation_time'] = instance_df['creation_time'].dt.time
    instance_df['committed_completion_time'] = instance_df['committed_completion_time'].dt.time
    
    # add pickup and delivery location
    instance_df['pickup_id'] = instance_df['restaurant_name']
    instance_df['delivery_id'] = instance_df['customer_name']
    
    instance_df.drop(['index'], axis=1, inplace=True)
    
    for index, row in instance_df.iterrows():
        instance_df.at[index, 'order_id'] = row['order_id'][-6:] + str(index).zfill(5)

    return instance_df

In [59]:
instance = instance_generation(restaurants=restaurants_select)
instance_df = instance[['order_id', 'demand', 'creation_time', 'committed_completion_time', 
                        'load_time', 'unload_time', 'pickup_id', 'delivery_id']]


instance_df

order_id  demand creation_time committed_completion_time  load_time  \
0     06042300000       1      06:04:23                  06:49:23         60   
1     06080500001       1      06:08:05                  06:53:05         60   
2     06083900002       1      06:08:39                  06:53:39         60   
3     06094400003       1      06:09:44                  06:54:44         60   
4     06095000004       1      06:09:50                  06:54:50         60   
...           ...     ...           ...                       ...        ...   
2486  22250602486       1      22:25:06                  23:10:06         60   
2487  22255602487       1      22:25:56                  23:10:56         60   
2488  22260502488       1      22:26:05                  23:11:05         60   
2489  22262002489       1      22:26:20                  23:11:20         60   
2490  22264302490       1      22:26:43                  23:11:43         60   

      unload_time                         pickup_id       delivery_id  
0              60     Ghim Moh Market & Food Centre  288408 Singapore  
1              60     Ghim Moh Market & Food Centre  597158 Singapore  
2              60  Bukit Timah Market & Food Centre  679409 Singapore  
3              60  Bukit Timah Market & Food Centre  678087 Singapore  
4              60     Ghim Moh Market & Food Centre  140023 Singapore  
...           ...                               ...               ...  
2486           60     Ghim Moh Market & Food Centre  590017 Singapore  
2487           60  Bukit Timah Market & Food Centre  659636 Singapore  
2488           60     Alexandra Village Food Centre  140023 Singapore  
2489           60  Bukit Timah Market & Food Centre  258822 Singapore  
2490           60     Ghim Moh Market & Food Centre  589652 Singapore  

[2491 rows x 8 columns]

In [60]:
instance_df.to_csv("Food_delivery_simulator/Benchmark/Instance_2/instance_2.csv", index=False)

## Get route information

In [61]:
instance_df['delivery_id'] = instance_df['delivery_id'].str.strip()
instance_df['pickup_id'] = instance_df['pickup_id'].str.strip()

/Users/larcuser/opt/anaconda3/envs/yjfkd/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/Users/larcuser/opt/anaconda3/envs/yjfkd/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [62]:
unique_pickup_id = instance_df['pickup_id'].unique()
unique_delivery_id = instance_df['delivery_id'].unique()
unique_pickup_id.shape, unique_delivery_id.shape

((3,), (791,))

In [63]:
instance['distance'] = 0.0

for index, row in instance.iterrows():
    try:
        instance.at[index, 'distance'] = hs.haversine(row['pick_up_coordinate'], row['delivery_coordinate'])
    except:
        continue

instance.head()

order_id  demand creation_time committed_completion_time  load_time  \
0  06042300000       1      06:04:23                  06:49:23         60   
1  06080500001       1      06:08:05                  06:53:05         60   
2  06083900002       1      06:08:39                  06:53:39         60   
3  06094400003       1      06:09:44                  06:54:44         60   
4  06095000004       1      06:09:50                  06:54:50         60   

   unload_time                         pickup_id       delivery_id  \
0           60     Ghim Moh Market & Food Centre  288408 Singapore   
1           60     Ghim Moh Market & Food Centre  597158 Singapore   
2           60  Bukit Timah Market & Food Centre  679409 Singapore   
3           60  Bukit Timah Market & Food Centre  678087 Singapore   
4           60     Ghim Moh Market & Food Centre  140023 Singapore   

                    restaurant_name     customer_name  \
0     Ghim Moh Market & Food Centre  288408 Singapore   
1     Ghim Moh Market & Food Centre  597158 Singapore   
2  Bukit Timah Market & Food Centre  679409 Singapore   
3  Bukit Timah Market & Food Centre  678087 Singapore   
4     Ghim Moh Market & Food Centre  140023 Singapore   

                     pick_up_coordinate         delivery_coordinate  distance  
0   (1.31099663218896, 103.78823030662)   (1.326193125, 103.812056)  3.141721  
1   (1.31099663218896, 103.78823030662)  (1.329597576, 103.7666863)  3.164458  
2  (1.33945242854685, 103.776007306701)  (1.370856277, 103.7726215)  3.512179  
3  (1.33945242854685, 103.776007306701)  (1.360616894, 103.7674991)  2.536330  
4   (1.31099663218896, 103.78823030662)   (1.29429994, 103.7997259)  2.253889

In [64]:
# customer_coordinate_dict
customer_coordinate_dict = {}

for q in unique_delivery_id:
    coordinate = instance[instance['delivery_id'] == q]['delivery_coordinate'].unique()[0]
    customer_coordinate_dict[q] = coordinate

len(customer_coordinate_dict)

791

In [65]:
%%time
route_info_list = []
all_locations = np.append(unique_pickup_id, unique_delivery_id)
location_coordinate_dict = {**restaurant_coordinate_dict, **customer_coordinate_dict}

# distance matrix
for p in all_locations:
    for q in all_locations:
        L = [p, q]
        p_coordinate = location_coordinate_dict[p]
        q_coordinate = location_coordinate_dict[q]
        L.append(round(hs.haversine(p_coordinate, q_coordinate),2))
        route_info_list.append(L)

print(len(route_info_list))
route_info_list

630436


[['Ghim Moh Market & Food Centre', 'Ghim Moh Market & Food Centre', 0.0],
 ['Ghim Moh Market & Food Centre', 'Bukit Timah Market & Food Centre', 3.44],
 ['Ghim Moh Market & Food Centre', 'Alexandra Village Food Centre', 3.29],
 ['Ghim Moh Market & Food Centre', '288408 Singapore', 3.14],
 ['Ghim Moh Market & Food Centre', '597158 Singapore', 3.16],
 ['Ghim Moh Market & Food Centre', '679409 Singapore', 6.88],
 ['Ghim Moh Market & Food Centre', '678087 Singapore', 5.98],
 ['Ghim Moh Market & Food Centre', '140023 Singapore', 2.25],
 ['Ghim Moh Market & Food Centre', '129960 Singapore', 2.23],
 ['Ghim Moh Market & Food Centre', '589484 Singapore', 3.2],
 ['Ghim Moh Market & Food Centre', '652194 Singapore', 6.14],
 ['Ghim Moh Market & Food Centre', '277504 Singapore', 1.0],
 ['Ghim Moh Market & Food Centre', '140064 Singapore', 1.64],
 ['Ghim Moh Market & Food Centre', '599506 Singapore', 2.22],
 ['Ghim Moh Market & Food Centre', '140021 Singapore', 2.36],
 ['Ghim Moh Market & Food Centr

In [66]:
route_info = pd.DataFrame(route_info_list, columns=['start_location_id', 'end_location_id', 'distance'])
route_info['time'] = route_info['distance'] * 120 
route_info['time'] = route_info['time'].apply(np.int64)
route_info

start_location_id                   end_location_id  \
0       Ghim Moh Market & Food Centre     Ghim Moh Market & Food Centre   
1       Ghim Moh Market & Food Centre  Bukit Timah Market & Food Centre   
2       Ghim Moh Market & Food Centre     Alexandra Village Food Centre   
3       Ghim Moh Market & Food Centre                  288408 Singapore   
4       Ghim Moh Market & Food Centre                  597158 Singapore   
...                               ...                               ...   
630431               598753 Singapore                  650141 Singapore   
630432               598753 Singapore                  118036 Singapore   
630433               598753 Singapore                  679521 Singapore   
630434               598753 Singapore                  650257 Singapore   
630435               598753 Singapore                  598753 Singapore   

        distance  time  
0           0.00     0  
1           3.44   412  
2           3.29   394  
3           3.14   376  
4           3.16   379  
...          ...   ...  
630431      2.55   306  
630432      9.20  1104  
630433      1.99   238  
630434      1.04   124  
630435      0.00     0  

[630436 rows x 4 columns]

In [74]:
%%time
route_info['route_code'] = str()

for index, row in route_info.iterrows():
    route_info.at[index, 'route_code'] = str(index).zfill(6)

first_col = route_info.pop('route_code')
route_info.insert(0, 'route_code', first_col)

route_info

CPU times: user 32.9 s, sys: 147 ms, total: 33.1 s
Wall time: 33.3 s


route_code              start_location_id  \
0          000000  Ghim Moh Market & Food Centre   
1          000001  Ghim Moh Market & Food Centre   
2          000002  Ghim Moh Market & Food Centre   
3          000003  Ghim Moh Market & Food Centre   
4          000004  Ghim Moh Market & Food Centre   
...           ...                            ...   
630431     630431               598753 Singapore   
630432     630432               598753 Singapore   
630433     630433               598753 Singapore   
630434     630434               598753 Singapore   
630435     630435               598753 Singapore   

                         end_location_id  distance  time  
0          Ghim Moh Market & Food Centre      0.00     0  
1       Bukit Timah Market & Food Centre      3.44   412  
2          Alexandra Village Food Centre      3.29   394  
3                       288408 Singapore      3.14   376  
4                       597158 Singapore      3.16   379  
...                                  ...       ...   ...  
630431                  650141 Singapore      2.55   306  
630432                  118036 Singapore      9.20  1104  
630433                  679521 Singapore      1.99   238  
630434                  650257 Singapore      1.04   124  
630435                  598753 Singapore      0.00     0  

[630436 rows x 5 columns]

In [75]:
route_info.to_csv('Food_delivery_simulator/Benchmark/route_info.csv', index=False)

## Customer and Restaurant infomation

In [78]:
# restaurant
select_restaurant_coordinate_dict = {}
for r in restaurant_coordinate_dict:
    if r in restaurants_select:
        select_restaurant_coordinate_dict[r] = restaurant_coordinate_dict[r]

restaurant_info_df = pd.DataFrame(list(select_restaurant_coordinate_dict.items()), columns=['restaurant_id', 'coordinate'])

restaurant_info_df['latitude'] = 0.0
restaurant_info_df['longitude'] = 0.0

for index, row in restaurant_info_df.iterrows():
    restaurant_info_df.at[index, 'latitude'] = row['coordinate'][0]
    restaurant_info_df.at[index, 'longitude'] = row['coordinate'][1]

restaurant_info_df = restaurant_info_df[['restaurant_id', 'latitude', 'longitude']]
restaurant_info_df['dispatch_radius'] = 5
restaurant_info_df['customer_radius'] = 5
restaurant_info_df['wait_time'] = 120
restaurant_info_df

restaurant_id  latitude   longitude  dispatch_radius  \
0     Ghim Moh Market & Food Centre  1.310997  103.788230                5   
1  Bukit Timah Market & Food Centre  1.339452  103.776007                5   
2     Alexandra Village Food Centre  1.286306  103.804493                5   

   customer_radius  wait_time  
0                5        120  
1                5        120  
2                5        120

In [79]:
restaurant_info_df.to_csv('Food_delivery_simulator/Benchmark/restaurant_info.csv', index=False)

In [80]:
# customer
customer_info_df = pd.DataFrame(list(customer_coordinate_dict.items()), columns=['customer_id', 'coordinate'])

customer_info_df['latitude'] = 0.0
customer_info_df['longitude'] = 0.0

for index, row in customer_info_df.iterrows():
    customer_info_df.at[index, 'latitude'] = row['coordinate'][0]
    customer_info_df.at[index, 'longitude'] = row['coordinate'][1]

customer_info_df = customer_info_df[['customer_id', 'latitude', 'longitude']]
customer_info_df

customer_id  latitude   longitude
0    288408 Singapore  1.326193  103.812056
1    597158 Singapore  1.329598  103.766686
2    679409 Singapore  1.370856  103.772621
3    678087 Singapore  1.360617  103.767499
4    140023 Singapore  1.294300  103.799726
..                ...       ...         ...
786  650141 Singapore  1.350442  103.743212
787  118036 Singapore  1.278735  103.791147
788  679521 Singapore  1.370472  103.777208
789  650257 Singapore  1.351171  103.757985
790  598753 Singapore  1.357286  103.765111

[791 rows x 3 columns]

In [81]:
customer_info_df.to_csv('Food_delivery_simulator/Benchmark/customer_info.csv', index=False)

## Driver information

In [76]:
number_of_driver = 20

driver_info_df = pd.DataFrame(columns=['car_num', 'capacity', 'operation_time', 'gps_id'])

driver_info_df['car_num'] = ['D_'+str(i) for i in range(1, number_of_driver+1)]
driver_info_df['capacity'] = 10
driver_info_df['operation_time'] = 24
driver_info_df['gps_id'] = ['G_'+str(i) for i in range(1, number_of_driver+1)]

driver_info_df

car_num  capacity  operation_time gps_id
0      D_1        10              24    G_1
1      D_2        10              24    G_2
2      D_3        10              24    G_3
3      D_4        10              24    G_4
4      D_5        10              24    G_5
5      D_6        10              24    G_6
6      D_7        10              24    G_7
7      D_8        10              24    G_8
8      D_9        10              24    G_9
9     D_10        10              24   G_10
10    D_11        10              24   G_11
11    D_12        10              24   G_12
12    D_13        10              24   G_13
13    D_14        10              24   G_14
14    D_15        10              24   G_15
15    D_16        10              24   G_16
16    D_17        10              24   G_17
17    D_18        10              24   G_18
18    D_19        10              24   G_19
19    D_20        10              24   G_20

In [77]:
driver_info_df.to_csv('Food_delivery_simulator/Benchmark/Instance_2/driver_info.csv', index=False)

## Batch instance generation

In [248]:
restaurants_select_2 = ['Lorong 8 Toa Payoh Hawker Centre', 
                        'Kovan Food Centre (209 Hougang Street 21)',
                        'Breadtalk Ihq, 30 Tai Seng St, Singapore 534013, Singapore',
                        'Bedok Interchange Hawker Centre',
                        'Old Airport Road Food Centre']

instance_2 = instance_generation(restaurants=restaurants_select_2)
instance_2

order_id         create_time  \
0     2021101006002200000 2021-10-10 06:00:22   
1     2021101006050800001 2021-10-10 06:05:08   
2     2021101006070000002 2021-10-10 06:07:00   
3     2021101006080500003 2021-10-10 06:08:05   
4     2021101006081100004 2021-10-10 06:08:11   
...                   ...                 ...   
3878  2021101022230703878 2021-10-10 22:23:07   
3879  2021101022231303879 2021-10-10 22:23:13   
3880  2021101022244403880 2021-10-10 22:24:44   
3881  2021101022254403881 2021-10-10 22:25:44   
3882  2021101022290203882 2021-10-10 22:29:02   

                                        restaurant_name  \
0             Kovan Food Centre (209 Hougang Street 21)   
1                      Lorong 8 Toa Payoh Hawker Centre   
2                       Bedok Interchange Hawker Centre   
3                          Old Airport Road Food Centre   
4                      Lorong 8 Toa Payoh Hawker Centre   
...                                                 ...   
3878  Breadtalk Ihq, 30 Tai Seng St, Singapore 53401...   
3879                       Old Airport Road Food Centre   
3880                       Old Airport Road Food Centre   
3881          Kovan Food Centre (209 Hougang Street 21)   
3882                    Bedok Interchange Hawker Centre   

                                 customer_name  \
0                             570175 Singapore   
1                             577531 Singapore   
2                             470106 Singapore   
3                             425671 Singapore   
4                             309074 Singapore   
...                                        ...   
3878  38 Chuan Pl, Singapore 554832, Singapore   
3879                          350145 Singapore   
3880                          358733 Singapore   
3881                          530018 Singapore   
3882                          461001 Singapore   

                        pick_up_coordinate         delivery_coordinate  
0     (1.35908384091048, 103.886055368064)   (1.348960622, 103.853736)  
1      (1.3402610461881, 103.854395758866)  (1.351929252, 103.8316427)  
2     (1.32481816551889, 103.930544296289)  (1.329501522, 103.9093817)  
3       (1.3082518471287, 103.88580870609)  (1.313012059, 103.9098686)  
4      (1.3402610461881, 103.854395758866)   (1.31741884, 103.8383834)  
...                                    ...                         ...  
3878            (1.334345265, 103.8896375)  (1.361268471, 103.8677606)  
3879    (1.3082518471287, 103.88580870609)  (1.332373178, 103.8661652)  
3880    (1.3082518471287, 103.88580870609)   (1.345958785, 103.868286)  
3881  (1.35908384091048, 103.886055368064)  (1.363216575, 103.8919296)  
3882  (1.32481816551889, 103.930544296289)   (1.327968792, 103.922716)  

[3883 rows x 6 columns]

# Visualization

In [193]:
m1 = folium.Map(location=[1.321537, 103.790782], tiles="Stamen Toner", zoom_start=13)

for r in ['Ghim Moh Market & Food Centre','Bukit Timah Market & Food Centre','Alexandra Village Food Centre']:
    l = [restaurant_coordinate_dict[r][0], restaurant_coordinate_dict[r][1]]
    folium.Marker(location=l, radius=50, color="#3186cc", popup=r).add_to(m1)
    folium.Circle(location=l, radius=5000).add_to(m1)


for index, row in instance.iterrows():
    if row['restaurant_name'] == 'Alexandra Village Food Centre':
        folium.Circle(location=row['delivery_coordinate'], radius=0.1, color='crimson').add_to(m1)

m1

In [185]:
restaurant_customer_dict['Ghim Moh Market & Food Centre'][1]

('276692 Singapore', (1.317735832, 103.7785544))

In [216]:
m2 = folium.Map(location=[1.321537, 103.790782], tiles="Stamen Toner", zoom_start=13)

for r in restaurants_select_2:
    l = [restaurant_coordinate_dict[r][0], restaurant_coordinate_dict[r][1]]
    folium.Marker(location=l, radius=50, color="#3186cc", popup=r).add_to(m2)
    folium.Circle(location=l, radius=5000).add_to(m2)


for index, row in instance_2.iterrows():
    # if row['restaurant_name'] == 'Alexandra Village Food Centre':
    folium.Circle(location=row['delivery_coordinate'], radius=0.1, color='crimson').add_to(m2)

m2

In [1]:
830 * 830

688900